<a href="https://colab.research.google.com/github/OmdenaAI/omdena-colombia-socialnetwork/blob/task-5-visualization/src/tasks/task-5-visualization/carlos_bar_chart_race.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
!pip install bar_chart_race -q

In [2]:
import pandas as pd 
import bar_chart_race as bcr

In [19]:
df = pd.read_csv("Corrected_final_all_with_sentiment.csv", index_col="Unnamed: 0", encoding="UTF-8")
df["hashtags"] = df["hashtags"].astype(str)
df["preprocessed_created_at"] = pd.to_datetime(df["preprocessed_created_at"])
df_es = df[df["lang"] == "es"]
df_en = df[df["lang"] == "en"]
df.head()

/usr/local/lib/python3.7/dist-packages/IPython/core/interactiveshell.py:2718: DtypeWarning: Columns (33) have mixed types.Specify dtype option on import or set low_memory=False.
  interactivity=interactivity, compiler=compiler, result=result)


created_at  ...  sentiment_score
0  2021-03-27T04:09:42+00:00  ...              1.0
1  2021-03-22T21:12:09+00:00  ...              1.0
2  2021-03-22T12:30:53+00:00  ...              0.0
3  2021-04-04T12:56:55+00:00  ...              0.0
4  2021-04-03T20:14:57+00:00  ...              1.0

[5 rows x 36 columns]

In [21]:
df_en.head()

created_at  ...  sentiment_score
16690  2021-04-23T07:14:36+00:00  ...              1.0
16691  2021-04-22T04:12:43+00:00  ...              0.0
16692  2021-04-22T04:12:00+00:00  ...              0.0
16693  2021-04-22T04:09:48+00:00  ...              0.0
16694  2021-04-22T03:32:26+00:00  ...              1.0

[5 rows x 36 columns]

In [22]:
df_es.head()

created_at  ...  sentiment_score
0  2021-03-27T04:09:42+00:00  ...              1.0
1  2021-03-22T21:12:09+00:00  ...              1.0
2  2021-03-22T12:30:53+00:00  ...              0.0
3  2021-04-04T12:56:55+00:00  ...              0.0
4  2021-04-03T20:14:57+00:00  ...              1.0

[5 rows x 36 columns]

In [47]:
def get_hashtag_counts(data): 
  counts_list = []
  for date in data["preprocessed_created_at"].unique():
    counts = {}
    counts["date"] = date
    sub_df = data[data["preprocessed_created_at"] == date]
    for _, row in sub_df.iterrows():
      for hashtag in row["hashtags"].split(","):
        hashtag = hashtag.replace("#","").strip()
        counts[hashtag] = counts.get(hashtag, 0) + 1
    counts_list.append(counts)
  return pd.DataFrame(counts_list)
hashtag_counts_es = get_hashtag_counts(df_es)
hashtag_counts_en = get_hashtag_counts(df_en)

In [48]:
hashtag_counts_es.set_index("date", inplace=True)
hashtag_counts_en.set_index("date", inplace=True)

hashtag_counts_es.sort_index(inplace=True)
hashtag_counts_en.sort_index(inplace=True)

hashtag_counts_es.fillna(0, inplace=True)
hashtag_counts_en.fillna(0, inplace=True)

hashtag_counts_es = hashtag_counts_es.astype(int)
hashtag_counts_en = hashtag_counts_en.astype(int)

hashtag_cumsum_es = hashtag_counts_es.cumsum(axis=0)
hashtag_cumsum_en = hashtag_counts_en.cumsum(axis=0)

del hashtag_cumsum_es["nan"]
del hashtag_cumsum_en["nan"]


In [49]:
hashtag_cumsum_es.to_csv("cumsum_es.csv")
hashtag_cumsum_en.to_csv("cumsum_en.csv")

In [50]:
hashtag_cumsum_es.head()

1mayo  Colombia  ...  uribecobarde  NoMasOspina
date                         ...                           
2021-03-22      0         0  ...             0            0
2021-03-23      0         0  ...             1            0
2021-03-24      0         0  ...             1            0
2021-03-25      0         5  ...             1            0
2021-03-26      0        24  ...             1            0

[5 rows x 7549 columns]

In [51]:
hashtag_cumsum_en.head()

1May  1maggio  1Mayo  ...  Indigenous  Misak  colombianlivesmatter
date                              ...                                         
2021-03-23     0        0      0  ...           0      0                     0
2021-03-28     0        0      0  ...           0      0                     0
2021-04-03     0        0      0  ...           0      0                     0
2021-04-07     0        0      1  ...           0      0                     0
2021-04-10     0        0      1  ...           0      0                     0

[5 rows x 649 columns]

In [56]:
def get_top_n_hashtags(data, n = 50):
  row = data.loc[data.index.max()]
  row = row.to_dict()
  hashtags_sorted = sorted(row.items(), key = lambda x: x[1], reverse = True)
  dict_hashtags = dict(hashtags_sorted[:n])
  return dict_hashtags.keys()

In [61]:
bcr.bar_chart_race(df=hashtag_cumsum_es[get_top_n_hashtags(hashtag_cumsum_es, 10)], figsize=(10.5,10), title="Hashtag counts for spanish tweets")

In [60]:
bcr.bar_chart_race(df=hashtag_cumsum_en[get_top_n_hashtags(hashtag_cumsum_en, 10)], figsize=(10.5,10), title="Hashtag counts for english tweets")